# 配置环境

查看显卡型号

In [1]:
!nvidia-smi

Sat Jun  1 12:17:38 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla T4                       Off | 00000000:00:04.0 Off |                    0 |
| N/A   41C    P8               9W /  70W |      0MiB / 15360MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [5]:
%cd /content

/content


In [4]:
!git clone https://github.com/qiumutongxue/ChatTTS.git

Cloning into 'ChatTTS'...
remote: Enumerating objects: 164, done.
remote: Counting objects: 100% (116/116), done.
remote: Compressing objects: 100% (69/69), done.
remote: Total 164 (delta 80), reused 58 (delta 47), pack-reused 48
Receiving objects: 100% (164/164), 2.73 MiB | 5.40 MiB/s, done.
Resolving deltas: 100% (86/86), done.


In [ ]:
%cd /content/ChatTTS

In [7]:
!pip install -r requirements.txt

安装WeTextProcessing，否则会报错

In [64]:
!pip install WeTextProcessing nemo_text_processing openai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 320.7/320.7 kB 6.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 10.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 5.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 6.0 MB/s eta 0:00:00


# 开始训练

## Load Models

In [29]:
%cd /content/ChatTTS

/content/ChatTTS


In [30]:
import torch
torch._dynamo.config.cache_size_limit = 64
torch._dynamo.config.suppress_errors = True
torch.set_float32_matmul_precision('high')

import ChatTTS
from IPython.display import Audio

In [31]:
chat = ChatTTS.Chat()
chat.load_models()

# Use force_redownload=True if the weights updated.
# chat.load_models(force_redownload=True)

# If you download the weights manually, set source='locals'.
# chat.load_models(source='local', local_path='YOUR LOCAL PATH')

## Batch infer 这里生成三句英文三句中文

In [38]:
texts = ["Hello everyone, I'm Mu You. Today, I want to introduce a very impressive TTS project. It has been released for less than a week, and by the time I'm writing this document, the project has already garnered 13.8K stars. I wonder if you can tell that this voice is actually generated by text-to-speech."]*3 \
+["大家好，我是沐柚，今天介绍一个非常厉害的TTS项目，发布了不到一周，到我写这个文档的时候，这个项目的start数量已经来到了十三点八K。不知道大家能不能听出来，这个声音其实是文本转语音出来的。"]*3

wavs = chat.infer(texts)

 48%|████▊     | 985/2048 [00:36<00:39, 27.25it/s]


In [44]:
Audio(wavs[1], rate=24_000, autoplay=False)

In [45]:
Audio(wavs[3], rate=24_000, autoplay=False)

In [46]:
Audio(wavs[4], rate=24_000, autoplay=False)

## Custom params

In [49]:
params_infer_code = {'prompt':'[speed_5]', 'temperature':.3} #设置语速，语气
params_refine_text = {'prompt':'[oral_2][laugh_0][break_6]'} #这里加随机的断句词
wav = chat.infer('永远不要提前焦虑，也不要提前预知烦恼，更不要被当下的情绪所消耗，那样会对你的身体造成很大的伤害，你只需要好好享受当下。车到山前必有路，关关难过关关过，揪着过去不放，不要不依不饶, 画地为牢，你要允许一切发生，调整好情绪，毕竟我们无法左右的事情太多，握不住的东西和留不住的人也太多，尽心尽力，顺其自然就好！', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)

 64%|██████▍   | 1310/2048 [00:40<00:22, 32.12it/s]


In [53]:
Audio(wav[0], rate=24_000, autoplay=False)

## Fix random speaker

In [55]:
rand_spk = chat.sample_random_speaker()
params_infer_code = {'spk_emb' : rand_spk, }  ## add sampled speaker
params_refine_text = {'prompt':'[oral_2][laugh_0][break_6]'} #这里加随机的断句词
wav = chat.infer('不要把时间浪费在尚未发生且没有必要的人和事上，更不要在焦虑和烦恼中度过，你要把时间分给睡眠，分给书籍，分给运动，分给音乐，分给花鸟树木山川湖泊，当你开始做时间的主人，那些焦虑和烦恼自然就烟消云散了。', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)

 46%|████▌     | 937/2048 [00:29<00:34, 32.00it/s]


In [56]:
Audio(wav[0], rate=24_000, autoplay=False)

## Two stage control

In [58]:
text = "晏子使楚，后来晏子离开的时候后面官员追着大喊：晏子，晏子，没有你我可怎么活呀"
chat.infer(text, refine_text_only=True)   #这里只是显示断句结果

 12%|█▎        | 48/384 [00:01<00:10, 33.10it/s]


['晏 子 使 楚 [uv_break] ， 后 来 晏 子 离 开 的 时 候 就 是 后 面 那 个 官 员 追 着 大 喊 ， 晏 子 ， 晏 子 ， 没 有 你 [uv_break] 那 我 可 怎 么 活 呀']

In [59]:
text= ["晏 子 使 楚 [uv_break] ， 后 来 晏 子 离 开 的 时 候 就 是 后 面 那 个 官 员 追 着 大 喊 ， 晏 子 ， [uv_break] 晏 子 ，  [uv_break]没 有 你 [uv_break] 那 我 可 怎 么 活 呀[laugh]"]*3
wav = chat.infer(text, skip_refine_text=True)   #设定不要自行断句，这里把上一行命令的断句后的文本粘贴到这里，不合适的地方进行修改。

 22%|██▏       | 453/2048 [00:14<00:50, 31.49it/s]


In [60]:
Audio(wav[0], rate=24_000, autoplay=False)

In [61]:
Audio(wav[1], rate=24_000, autoplay=False)

In [62]:
Audio(wav[2], rate=24_000, autoplay=False)

## LLM Call

In [65]:
from ChatTTS.experimental.llm import llm_api

API_KEY = 'sk-26d9a36137854bdd98cbd3d187d21479'
client = llm_api(api_key=API_KEY,
        base_url="https://api.deepseek.com",
        model="deepseek-chat")

In [66]:
rand_spk = chat.sample_random_speaker()
user_question = '四川有哪些好吃的美食呢?'
text = client.call(user_question, prompt_version = 'deepseek')
print(text)
# text = client.call(text, prompt_version = 'deepseek_TN')
# print(text)

四川美食可多了, 有麻辣火锅、宫保鸡丁、回锅肉、麻婆豆腐、担担面、夫妻肺片、串串香、宜宾燃面、乐山钵钵鸡、绵阳米粉等等, 每样都让人垂涎三尺。


In [67]:
params_infer_code = {'spk_emb' : rand_spk, 'temperature':.3}

wav = chat.infer(text, params_infer_code=params_infer_code)

 32%|███▏      | 659/2048 [00:22<00:48, 28.91it/s]


In [68]:
Audio(wav[0], rate=24_000, autoplay=False)